In [5]:
!pip install langchain qdrant_client openai tiktoken
!pip install -U langchain-openai

  Obtaining dependency information for langchain-openai from https://files.pythonhosted.org/packages/73/c0/bded8320fb0bbaeb3383fa8a45c287b95e153566f4ba2b749a67074090e5/langchain_openai-0.3.21-py3-none-any.whl.metadata
  Obtaining dependency information for langchain-core<1.0.0,>=0.3.64 from https://files.pythonhosted.org/packages/c3/43/94b486eeb778443887e4eb76326e704ee0c6244f5fab6a46686e09968e9a/langchain_core-0.3.64-py3-none-any.whl.metadata
  Obtaining dependency information for openai<2.0.0,>=1.68.2 from https://files.pythonhosted.org/packages/2a/10/f245db006a860dbc1f2e2c8382e0a1762c7753e7971ba43a1dc3f3ec1404/openai-1.84.0-py3-none-any.whl.metadata
  Obtaining dependency information for tiktoken<1,>=0.7 from https://files.pythonhosted.org/packages/6f/07/c67ad1724b8e14e2b4c8cca04b15da158733ac60136879131db05dda7c30/tiktoken-0.9.0-cp311-cp311-win_amd64.whl.metadata
  Obtaining dependency information for langsmith<0.4,>=0.3.45 from https://files.pythonhosted.org/packages/6a/f4/c206c0888

ERROR: Could not install packages due to an OSError: [WinError 5] Access is denied: 'C:\\Users\\mered\\anaconda3\\Lib\\site-packages\\~standard\\backend_c.cp311-win_amd64.pyd'
Consider using the `--user` option or check the permissions.



Run this notebook when you have a new set of source documents and need to:
<br>>load documents
<br>>split text
<br>>embed
<br>>store in Qdrant collection
<br><br>You will then call the vector store from the app_name.py file

In [6]:
from dotenv import load_dotenv
import streamlit as st
from langchain.vectorstores import Qdrant
from langchain_openai import OpenAIEmbeddings
from langchain.chains import RetrievalQA
from langchain.llms import OpenAI
from qdrant_client import QdrantClient, models
import qdrant_client
from langchain_community.document_loaders import PyPDFLoader
# from PyPDF2 import PdfReader
from langchain_text_splitters import RecursiveCharacterTextSplitter
import os

In [7]:
#OpenAI api key
openai_api_key = st.secrets["OPENAI_API_KEY"]

# Create a Qdrant client
client = qdrant_client.QdrantClient(
    st.secrets["QDRANT_HOST"],
    api_key=st.secrets["QDRANT_API_KEY"]
    )

# embedding a document
embeddings = OpenAIEmbeddings(
    api_key=openai_api_key,
    model="text-embedding-3-large"
)

In [4]:
# delete collection

client.delete_collection(collection_name=st.secrets["QDRANT_COLLECTION_NAME"])

True

In [9]:
# create collection
vectors_config = models.VectorParams(
    size=3072, # maybe 3072 for vector size OpenAI text-embedding-3-large. 1536 OpenAI text-embeddings-3-small.
    distance=models.Distance.COSINE, #telling Qdrant which distance to find siliarity in search
    on_disk=True, # need this for the binary quantization attempt 
)

client.create_collection( # may need to be recreate_collection
    collection_name=st.secrets["QDRANT_COLLECTION_NAME"],
    vectors_config=vectors_config,
    optimizers_config = models.OptimizersConfigDiff( #setting indexing threshold to 0. Disabling the indexing to zero. 
                                                    # Allows faster vector uploads and paylods. Turn back on lower in code.
        default_segment_number=5,
        indexing_threshold=0,
    ),
    quantization_config = models.BinaryQuantization(
        binary=models.BinaryQuantizationConfig(always_ram=True),
    ),
)


UnexpectedResponse: Unexpected Response: 404 (Not Found)
Raw response content:
b'404 page not found\n'

In [6]:
#create vector store
vector_store = Qdrant(
    client = client,
    collection_name = st.secrets["QDRANT_COLLECTION_NAME"],
    embeddings = embeddings,
)

In [7]:
# Define the directory where source documents are stored
directory = 'PDFs_and_TXT'

In [8]:

# Define function to load source documents from directory
def load_sources(directory):
    documents = []
    for filename in os.listdir(directory):
        if filename.endswith('.pdf'):
            file_path = os.path.join(directory, filename)
            try:
                loader = PyPDFLoader(file_path)
                doc = loader.load()
                documents.extend(doc)
                print(f"processed document: {filename}")
            except Exception as e:
                print(f"failed to process {filename}: {str(e)}")
            
    return documents

In [9]:
#test load_sources function
loaded_documents = load_sources(directory)
print(loaded_documents)

processed document: KPMG_Leases_Handbook_05_31_2023.pdf
[Document(page_content=' \nLeases \n \nHandbook  \n \n \n \nUS GAAP  \n \nMay 2023  \n______  \nfrv.kpmg.us  ', metadata={'source': 'PDFs_and_TXT\\KPMG_Leases_Handbook_05_31_2023.pdf', 'page': 0}), Document(page_content='Contents \nForeword  ............................................................................................................... 1 \nAbout this publication  ........................................................................................... 2 \n1.  Executive summary ........................................................................................ 5 \n2.  Scope  ........................................................................................................... 15 \n3. Definition of a lease ...................................................................................... 33 \n4.  Separating components of a contract  ........................................................ 146 \n5. Con

each chunk has meta data with document source and page number. Here is an example:

nAn entity shall disclose all of the following in the fiscal per iod in which a  change in accounting 
\nprinciple  is made:', metadata={'source': 'PDFs_and_TXT\\PWC-pwcleasesguide0124.pdf', 'page': 347})

In [10]:
# chunk pdfs
# each chunk has meta data with document source and page number. Here is an example:

# nAn entity shall disclose all of the following in the fiscal per iod in which a  change in accounting 
# \nprinciple  is made:', metadata={'source': 'PDFs_and_TXT\\PWC-pwcleasesguide0124.pdf', 'page': 347})


def chunk_pdfs(documents):
    text_splitter = RecursiveCharacterTextSplitter(
        chunk_size = 10000,
        chunk_overlap = 200
    )
    
    chunks = text_splitter.split_documents(documents)
    return chunks

In [11]:
chunks = chunk_pdfs(loaded_documents)
print(chunks)

[Document(page_content='Leases \n \nHandbook  \n \n \n \nUS GAAP  \n \nMay 2023  \n______  \nfrv.kpmg.us', metadata={'source': 'PDFs_and_TXT\\KPMG_Leases_Handbook_05_31_2023.pdf', 'page': 0}), Document(page_content='Contents \nForeword  ............................................................................................................... 1 \nAbout this publication  ........................................................................................... 2 \n1.  Executive summary ........................................................................................ 5 \n2.  Scope  ........................................................................................................... 15 \n3. Definition of a lease ...................................................................................... 33 \n4.  Separating components of a contract  ........................................................ 146 \n5. Concepts and definitions for lessees and lessors  ..............

In [12]:
# add embedded chunks to vector store. I think this process does the embedding?
vector_store.add_documents(chunks)

['d064cb6264b74f0f974946c3b60e9475',
 'e36c6622807a40128cee012f3f35e296',
 '7714d68b69cd4531b60a90c2ccbf6a19',
 '8040073c939f423ea96ae6453bbcccd2',
 '2a327d60d7cd43f8ad0d445108e28280',
 '5ed8fb7043bc48d594490982e1215b6d',
 'f85c34deb0b749f49ab564f7b314456d',
 '2c0a3c4d3a2d4ac38305dd9ef30914bc',
 '17a537a8232a4112855ce77e9942d23f',
 '450d89b6d9e44e419fce3b7d87b63916',
 '9058cde9db58413c8c5e73665f6d5326',
 '72e66f6ec7da466e8c1080fe343c3b11',
 'fa1d7e27c2cd40ffa071b3e8b10b4225',
 '1d6d195ee987477f8702173c2adcef00',
 '3343d94bdb49439a943165ba41bc4c6d',
 'c4d9dd57629c408793dd4d226728b5fe',
 'b446508085634a3299901f75531d436d',
 'd21d7804122949309b06371012040aee',
 '12be53850f7a435bb89a09874abd3b1a',
 '9c8311d6870843649763028a53dfb913',
 '41b3e6da600d406590ce8b35670d2f30',
 '96f32eb1d9654d29a1eeee7742de1f28',
 '31e58b49d0aa4749a9dcc4c64fb0250c',
 'f092626221e949e19a07e69f31e59944',
 '9ba878f22c64451e8cd8873cb30760a0',
 '51abb7c7487647e889da7de0c3ae5bb6',
 '7d728cc6e0bb4fc7920d680b41b64e11',
 

In [13]:
# Enable indexing again after upload vectors

client.update_collection(
    collection_name=st.secrets["QDRANT_COLLECTION_NAME"],
    optimizer_config=models.OptimizersConfigDiff(
        indexing_threshold=20000
    )
)

True

In [14]:
# this function uses PdfReader instead because then it allows for removing the /n characters. But it turns out,
# the recursive text splitter uses the /n characters for splitting. And my chunking function relies on the format of 
# a (list?) with page_content in it. I gues it's not a list, maybe a list of tuples?

# # Define function to load source documents from directory
# def load_sources(directory):
#     documents = []
#     for filename in os.listdir(directory):
#         if filename.endswith('.pdf'):
#             file_path = os.path.join(directory, filename)
#             try:
#                 reader = PdfReader(file_path)
#                 text = ''
#                 for page in reader.pages:
#                     text += page.extract_text() + ' '  # Add a space between pages
#                 # Clean text: replace line breaks with spaces, then normalize whitespace
#                 cleaned_text = text.replace('\n', ' ').replace('\r', ' ')
#                 cleaned_text = ' '.join(cleaned_text.split())
#                 documents.append(cleaned_text)
#             except Exception as e:
#                 print(f"Failed to process {filename}: {str(e)}")
#     return documents

# # Example usage
# documents = load_sources(directory)
# print(documents)